# Installs & Imports

In [1]:
!pip install -q deap

In [2]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from deap import base, creator, tools, algorithms
from sklearn.datasets import load_iris
from sklearn.model_selection import cross_val_score, StratifiedKFold
from sklearn.svm import SVC
import logging
import sys
from IPython.display import HTML

# Set up logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s', force=True)

# Load the Data

In [3]:
# Function to load the data
def load_data():
    """Load the dataset."""
    data = load_iris()
    X, y = data.data, data.target
    logging.info("Loaded Iris dataset.")
    return X, y

In [4]:
# Load the data
X, y = load_data()

2024-08-26 02:44:37,860 - INFO - Loaded Iris dataset.


# Create the Toolbox

In [5]:
# Function to create the toolbox
def create_toolbox():
    """Create the DEAP toolbox with the appropriate settings."""
    creator.create("FitnessMulti", base.Fitness, weights=(-1.0, 1.0))  # Minimize error, maximize simplicity
    creator.create("Individual", list, fitness=creator.FitnessMulti)

    toolbox = base.Toolbox()
    toolbox.register("attr_C", np.random.uniform, 1e-3, 1e+3)  # Log-scale range for C
    toolbox.register("attr_gamma", np.random.uniform, 1e-3, 1e+3)  # Log-scale range for gamma
    toolbox.register("attr_kernel", np.random.choice, ['linear', 'rbf'])
    toolbox.register("individual", tools.initCycle, creator.Individual,
                     (toolbox.attr_C, toolbox.attr_gamma, toolbox.attr_kernel), n=1)
    toolbox.register("population", tools.initRepeat, list, toolbox.individual)

    logging.info("Toolbox created.")
    return toolbox

In [6]:
# Create toolbox
toolbox = create_toolbox()

2024-08-26 02:44:37,897 - INFO - Toolbox created.


# NSGA-II Optimization

In [7]:
# Function to evaluate an individual's fitness
def evaluate(individual, X, y):
    """Evaluate the fitness of an individual."""
    C, gamma, kernel = individual
    svc = SVC(C=C, gamma=gamma if kernel == 'rbf' else 'scale', kernel=kernel)

    # Use stratified K-fold to ensure balanced classes in each fold
    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    accuracy = cross_val_score(svc, X, y, cv=cv, scoring='accuracy').mean()

    # Define complexity as a product of hyperparameters
    complexity = C * gamma if kernel == 'rbf' else C

    logging.debug(f"Evaluated individual: {individual}, Accuracy: {accuracy}, Complexity: {complexity}")

    return -accuracy, complexity

In [8]:
# Function to perform crossover operation
def custom_crossover(ind1, ind2):
    """Custom crossover function to handle both continuous and categorical variables."""
    # Continuous parameters (C, gamma) with cxBlend
    for i in range(2):
        gamma = np.random.uniform(-0.5, 1.5)
        ind1[i] = max(1e-3, min((1 - gamma) * ind1[i] + gamma * ind2[i], 1e+3))
        ind2[i] = max(1e-3, min(gamma * ind1[i] + (1 - gamma) * ind2[i], 1e+3))

    # Categorical parameter (kernel)
    if np.random.rand() < 0.5:
        ind1[2], ind2[2] = ind2[2], ind1[2]

    return ind1, ind2

In [9]:
# Function to perform mutation operation
def custom_mutation(individual, mu, sigma, indpb):
    """Custom mutation function to handle both continuous and categorical variables."""
    # Mutate continuous parameters (C, gamma)
    for i in range(2):
        if np.random.rand() < indpb:
            individual[i] += np.random.normal(mu, sigma)
            # Ensure parameters stay within the allowed range
            individual[i] = max(1e-3, min(individual[i], 1e+3))

    # Mutate categorical parameter (kernel)
    if np.random.rand() < indpb:
        individual[2] = 'linear' if individual[2] == 'rbf' else 'rbf'

    return individual,

In [10]:
# Function to run the optimization
def run_nsga2_optimization(toolbox, X, y, n_gen=50, pop_size=100):
    """Run NSGA-II optimization and return the final population, logbook, and history of both the entire population and Pareto front."""
    logging.info(f"Starting NSGA-II optimization with {n_gen} generations and population size {pop_size}.")

    toolbox.register("mate", custom_crossover)
    toolbox.register("mutate", custom_mutation, mu=0, sigma=0.1, indpb=0.2)
    toolbox.register("select", tools.selNSGA2)
    toolbox.register("evaluate", evaluate, X=X, y=y)

    population = toolbox.population(n=pop_size)
    hall_of_fame = tools.HallOfFame(1, similar=np.array_equal)

    stats = tools.Statistics(lambda ind: ind.fitness.values)
    stats.register("avg", np.mean, axis=0)
    stats.register("std", np.std, axis=0)
    stats.register("min", np.min, axis=0)
    stats.register("max", np.max, axis=0)

    logbook = tools.Logbook()

    population_history = []
    pareto_history = []

    for gen in range(n_gen):
        logging.info(f"Generation {gen+1}/{n_gen}")
        sys.stdout.flush()

        offspring = algorithms.varOr(population, toolbox, lambda_=pop_size * 2, cxpb=0.6, mutpb=0.3)
        invalid_ind = [ind for ind in offspring if not ind.fitness.valid]
        fitnesses = toolbox.map(toolbox.evaluate, invalid_ind)
        for ind, fit in zip(invalid_ind, fitnesses):
            ind.fitness.values = fit

        population = toolbox.select(offspring, pop_size)

        # Save both the entire population and the Pareto front of this generation
        population_history.append(list(population))
        pareto_front = tools.sortNondominated(population, len(population), first_front_only=True)[0]
        pareto_history.append(list(pareto_front))

        record = stats.compile(population)
        logbook.record(gen=gen, nevals=len(invalid_ind), **record)
        if hall_of_fame is not None:
            hall_of_fame.update(population)

        print(f"Avg Fitness: {record['avg']}, Min Fitness: {record['min']}, Max Fitness: {record['max']}\n")
        sys.stdout.flush()

    logging.info("Optimization complete.")
    return population, logbook, population_history, pareto_history

In [11]:
# Run NSGA-II optimization
n_gen = 100
pop_size = 200
population, logbook, population_history, pareto_history = run_nsga2_optimization(toolbox, X, y, n_gen, pop_size)

2024-08-26 02:44:37,981 - INFO - Starting NSGA-II optimization with 100 generations and population size 200.
2024-08-26 02:44:37,993 - INFO - Generation 1/100


Avg Fitness: [-6.28600000e-01  2.35952836e+05], Min Fitness: [-0.98666667  0.34329202], Max Fitness: [-3.93333333e-01  1.00000000e+06]



2024-08-26 02:44:55,155 - INFO - Generation 2/100


Avg Fitness: [-5.82700000e-01  2.34478924e+05], Min Fitness: [-0.98666667  0.12411246], Max Fitness: [-3.93333333e-01  9.91083195e+05]



2024-08-26 02:45:06,671 - INFO - Generation 3/100


...

2024-08-26 02:54:57,993 - INFO - Generation 99/100


Avg Fitness: [-8.69333333e-01  4.14161825e+04], Min Fitness: [-0.98666667  1.        ], Max Fitness: [-3.93333333e-01  1.00000000e+06]



2024-08-26 02:55:04,102 - INFO - Generation 100/100


Avg Fitness: [-8.96133333e-01  3.37284695e+04], Min Fitness: [-0.98666667  1.        ], Max Fitness: [-3.93333333e-01  1.00000000e+06]



2024-08-26 02:55:09,925 - INFO - Optimization complete.


# Animate the Results

In [12]:
# Function to prepare the animation data
def prepare_animation_data(history):
    """Prepare data for the animation."""
    fitness_history = [np.array([ind.fitness.values for ind in gen]) for gen in history]
    logging.debug(f"Prepared animation data for {len(history)} generations.")
    return fitness_history

In [13]:
# Prepare data for animations
population_fitness_history = prepare_animation_data(population_history)
pareto_fitness_history = prepare_animation_data(pareto_history)

In [14]:
# Function to create the animation
def create_animation(fitness_history, n_gen, title, output_file=None):
    """Create and save the Pareto front animation."""
    logging.info(f"Creating animation and saving to {output_file if output_file else 'inline display'}.")
    fig, ax = plt.subplots(figsize=(10, 6))
    scat = ax.scatter([], [], s=60)

    # Determine global limits based on all generations
    x_min = min(np.min(fitness[:, 0]) for fitness in fitness_history)
    x_max = max(np.max(fitness[:, 0]) for fitness in fitness_history)
    y_min = min(np.min(fitness[:, 1]) for fitness in fitness_history)
    y_max = max(np.max(fitness[:, 1]) for fitness in fitness_history)

    ax.set_xlim([x_min * 0.9, x_max * 1.1])
    ax.set_ylim([y_min * 0.9, y_max * 1.1])
    ax.set_xlabel('Cross-Validation Error')
    ax.set_ylabel('Model Complexity')
    ax.set_title(title)

    def update(frame):
        x = fitness_history[frame][:, 0]
        y = fitness_history[frame][:, 1]
        scat.set_offsets(np.c_[x, y])
        return scat,

    ani = animation.FuncAnimation(fig, update, frames=n_gen, interval=200, blit=False)

    if output_file:
        ani.save(output_file, writer='imagemagick')
    else:
        plt.close(fig)
        return ani.to_jshtml()

    plt.show()
    logging.info("Animation created and displayed.")

In [15]:
# Display the animation for the entire population
HTML(create_animation(population_fitness_history, n_gen, 'Population Evolution - NSGA-II'))

2024-08-26 02:55:10,081 - INFO - Creating animation and saving to inline display.
2024-08-26 02:55:10,126 - INFO - Animation.save using <class 'matplotlib.animation.HTMLWriter'>


In [16]:
# Display the animation for the Pareto front
HTML(create_animation(pareto_fitness_history, n_gen, 'Pareto Front Evolution - NSGA-II'))

2024-08-26 02:55:22,359 - INFO - Creating animation and saving to inline display.
2024-08-26 02:55:22,399 - INFO - Animation.save using <class 'matplotlib.animation.HTMLWriter'>


# Evaluate the Model

In [17]:
# Extract the Pareto front from the last generation's population
pareto_front = tools.sortNondominated(population, len(population), first_front_only=True)[0]

# Select the best individual based on the first objective
best_individual = max(pareto_front, key=lambda ind: ind.fitness.values[0])

In [18]:
# Extract the hyperparameters from the best individual
best_hyperparameters = {
    'C': best_individual[0],
    'gamma': best_individual[1],
    'kernel': best_individual[2]
}

print("Best hyperparameters found: ", best_hyperparameters)

Best hyperparameters found:  {'C': 1000.0, 'gamma': 1000.0, 'kernel': 'rbf'}


In [19]:
# Define weights for each objective
weights = [0.7, 0.3]

# Calculate the weighted sum for each individual in the Pareto front
def weighted_sum(individual, weights):
    return sum(w * f for w, f in zip(weights, individual.fitness.values))

# Select the best individual based on the weighted sum of objectives
best_individual = max(pareto_front, key=lambda ind: weighted_sum(ind, weights))

# Extract the hyperparameters from the best individual
best_hyperparameters = {
    'C': best_individual[0],
    'gamma': best_individual[1],
    'kernel': best_individual[2]
}

print("Best hyperparameters found based on weighted sum: ", best_hyperparameters)

Best hyperparameters found based on weighted sum:  {'C': 1000.0, 'gamma': 1000.0, 'kernel': 'rbf'}


In [20]:
# Create the final model using the best hyperparameters
final_model = SVC(C=best_hyperparameters['C'],
                  gamma=best_hyperparameters['gamma'] if best_hyperparameters['kernel'] == 'rbf' else 'scale',
                  kernel=best_hyperparameters['kernel'])

# Train the model on the entire dataset
final_model.fit(X, y)

# Evaluate the model
accuracy = final_model.score(X, y)
print("Final model accuracy: ", accuracy)

Final model accuracy:  1.0


In [21]:
# Train multiple models
best_accuracy = 0
best_model = None

for individual in pareto_front:
    hyperparameters = {
        'C': individual[0],
        'gamma': individual[1],
        'kernel': individual[2]
    }

    model = SVC(C=hyperparameters['C'],
                gamma=hyperparameters['gamma'] if hyperparameters['kernel'] == 'rbf' else 'scale',
                kernel=hyperparameters['kernel'])

    model.fit(X, y)

    # Cross-validate
    accuracy = cross_val_score(model, X, y, cv=5, scoring='accuracy').mean()

    if accuracy > best_accuracy:
        best_accuracy = accuracy
        best_model = model
        best_hyperparameters = hyperparameters

# Print the best model's hyperparameters and accuracy
print("Best model hyperparameters: ", best_hyperparameters)
print("Best model accuracy: ", best_accuracy)

Best model hyperparameters:  {'C': 1000.0, 'gamma': 0.001, 'kernel': 'rbf'}
Best model accuracy:  0.9800000000000001
